In [1]:
from ipywidgets import interact, interactive, fixed, interact_manual, Output
import ipywidgets as widgets
import IPython
from IPython.display import clear_output, display
from array import array
from ctypes import string_at
import aa
from ana import search
import ROOT

rasafile = aa.aadir + "/ana/search/effa/output/40bins/"
rasafile += "TFile_alldirections_zen_noanglecut_noloirecocut_f200_b40.root"
response = ROOT.DefaultDetResponse(rasafile)
bg_component = ROOT.BackgroundComponent( "bg_component", response )

objlist = ["response","bg_component"]


def pad_to_img ( pad ) :
    
    "convert ROOT pad to img that can be displayed by ipython "
    
    image = ROOT.TImage.Create()
    image.FromPad( pad )
    x,y = array('l', [0]),array('i', [0])
    image.GetImageBuffer(x,y, ROOT.TImage.kPng)
    s = string_at( x[0],y[0]) 
    img = IPython.display.Image( s, format='png' )
    return img            
     
    
def get_pdfs_from_object ( obj ) :
    
    "return all the methods of ROOT object that look like an interesting function to plot "    
    
    r = {}
    typename = obj.__class__.__name__
    
    for m in ROOT.TClass.GetClass( typename ).GetListOfMethods() :
        if 'dP_' in m.GetName() or 'dN_' in m.GetName() :
            m.argtypes = [ m.GetTypeName() for m in m.GetListOfMethodArgs() ]
            m.argnames = [ m.GetName()     for m in m.GetListOfMethodArgs() ]
           
            # select functions with numerical inputs (todo: check return type too)
            if all( t in ['double','int','float'] for t in m.argtypes ) :
                r[ m.GetName() ] = m
                
    return r
        


def get_range( name ) :
    
    "heuristic to return range and step-size based on parameter name."
    
    if name.startswith("log_reco_error") : return (-3.0, 3.0, 0.1)
    if name.startswith("reco_error") : return (0,180, 1 )
    if name.startswith("E") : return (2.0,8.0, 0.1 )
    if name.startswith("cos") : return (-0.8, 1.0, 0.1 )
    print ("don't know about parameter",name)
    return None
    
    
pdfs = get_pdfs_from_object( response )
   
# The following lets you select an object from 'objlist', then you
# can select a method of that object that you want to plot. Then
# you can select the variable on the x-axis; the other varaibles
# will have sliders where you can set the value.
    
def select_object( objname ) :
    
    obj = globals()[objname]
    funcs = get_pdfs_from_object( obj )
    
    # print(objname, obj, funcs)
    
    def select_func( methodname ) :

        pdf = funcs[methodname]

        def select_x_axis( x_axis ) :

            n = pdf.argnames.index( x_axis )  
            otherargs = pdf.argnames[:n] + pdf.argnames[n+1:]

            r = get_range( x_axis )
            h = ROOT.TH1D("h","h;"+x_axis, 30, r[0],r[1] )
            h.SetDirectory(0)

            def make_plot (logy, **args) :

                argvals = list( args.values() )

                def fun( x ) :
                    a = argvals[:n] + [x] + argvals[n:]
                    
                    # doesn't look like it, but : call the actuall function! 
                    return getattr( obj , methodname ) ( *a ) 

                for b in range( 1, h.GetNbinsX() + 1 ) :
                    h.SetBinContent( b, fun ( h.GetBinCenter(b) ))

                h.SetTitle( methodname +  str(args) )
                h.SetLineWidth(2)
                if ROOT.gPad : ROOT.gPad.SetLogy( logy )
                h.Draw("L")

                with out : 
                   img = pad_to_img( ROOT.gPad )
                   display(img)

            kk = { arg : get_range(arg) for arg in otherargs } # order preserved in > py3.5
            output_widget = interactive( make_plot , logy = False, **kk )

            # out is the place where the hisogram will be displayed
            out = output_widget.children[-1]
            # if you wanna write css (right!), you can 
            # out.layout = { 'width': '700px', 'height': '600px', 'border': '3px solid blue' }

            # display the sliders defined by kk   
            display(output_widget) 


        interact( select_x_axis , x_axis = pdf.argnames )

    interact( select_func, methodname = funcs.keys() );

interact( select_object, objname = objlist )

loading root....  /pbs/throng/km3net/software/root/6.20.04
Welcome to JupyROOT 6.20/04
loading /pbs/home/h/heijboer/aanet/lib/libaaevt.so ... ok (0.21 s.)
loading /pbs/home/h/heijboer/aanet/lib/libaastro.so ... ok (0.02 s.)
 welcome to aanet v2.1.0-7-g8622a30
loading /pbs/home/h/heijboer/aanet/lib/aasearch.so ... ok (0.04 s.)


interactive(children=(Dropdown(description='objname', options=('response', 'bg_component'), value='response'),…

<function __main__.select_object(objname)>